# Quantum Circuit Design through Monte Carlo Tree Search
In this tutorial we are going show the whole pipeline of the Monte Carlo Tree Search (MCTS) implemented for Quantum circuit Design.

## Problem Definition
First of all we need to assign a goal to the algorithm, namely we need to define an objective function to optimize. The objective function is a real-valued function defined on quantum circuits. You can find examples in the field of quantum chemistry, systems of linear equations, Sudoku and on random quantum circuit in the file evaluation_functions.py. 

Let's take as example the problem of finding the ground state energy of molecules, by using the variational quantum eigensolver.Let' take the simplest molecule $H_2$ as example. In the following we create a random quantum circuit and then evaluate it as a solution for the ground state problem of the hydrogen.

In [18]:
from qiskit import QuantumCircuit
import evaluation_functions as evf

qc = QuantumCircuit(4)
for i in range(4):
    qc.ry(0.5, i)

problem = evf.h2
cost_value = problem(qc, cost=True)

print(f"Given the quantum circuit below: \n{qc}\n the objective function returns: {cost_value}")

Given the quantum circuit below: 
     ┌─────────┐
q_0: ┤ Ry(0.5) ├
     ├─────────┤
q_1: ┤ Ry(0.5) ├
     ├─────────┤
q_2: ┤ Ry(0.5) ├
     ├─────────┤
q_3: ┤ Ry(0.5) ├
     └─────────┘
 the objective function returns: 0.5585648835784067


## Ansatz Search
Once we have defined the problem, we can use MCTS in order to design a suitable guess for the initial quantum circuit solving the problem. Then later we will use a classical optimizer in order to finetune the parameter.
First we need to fixed the hyperparameters of the model. See example below:

In [19]:
variable_qubits = 4
ancilla_qubits = 0
max_depth = 10
budget = 5000
branches = False
criteria = "average_value"
rollout_type = 'classic'
roll_out_steps = 2
choices = {'a': 50, 'd': 10, 's': 20, 'c': 20, 'p': 0}
epsilon = None
stop_deterministic = False
ucb = 0.4
pw_C = 5
pw_alpha = 0.3


Then, we can define the root node with the initial quantum circuit. The search starts from that node and finally it outputs the best path starting from the root to the leaf that creates the best circuit

In [20]:
import mcts
from structure import Circuit
root = mcts.Node(Circuit(variable_qubits=variable_qubits, ancilla_qubits=ancilla_qubits), max_depth=max_depth)
        
best_path = mcts.mcts(root, budget=budget, branches=branches, evaluation_function=problem, criteria=criteria, rollout_type=rollout_type, roll_out_steps=roll_out_steps,
                                choices=choices, epsilon=epsilon, stop_deterministic=stop_deterministic, ucb_value=ucb, pw_C=pw_C, pw_alpha=pw_alpha, verbose=True)

Root Node:
 Tree depth: 0  -  Generated by Action: None  -  Number of Children: 0  -  Visits: 0  -  Value: 0  -  Quantum Circuit (CNOT counts)= 0):
     ┌───┐
v_0: ┤ H ├
     ├───┤
v_1: ┤ H ├
     ├───┤
v_2: ┤ H ├
     ├───┤
v_3: ┤ H ├
     └───┘
Epoch Counter:  0
Node Expanded:
 Tree depth: 1  -  Generated by Action: a  -  Number of Children: 0  -  Visits: 0  -  Value: 0  -  Quantum Circuit (CNOT counts)= 0):
     ┌───┐              
v_0: ┤ H ├──────────────
     ├───┤┌────────────┐
v_1: ┤ H ├┤ Ry(1.3439) ├
     ├───┤└────────────┘
v_2: ┤ H ├──────────────
     ├───┤              
v_3: ┤ H ├──────────────
     └───┘              
Reward:  -0.0831548623692088
Epoch Counter:  1
Node Expanded:
 Tree depth: 1  -  Generated by Action: a  -  Number of Children: 0  -  Visits: 0  -  Value: 0  -  Quantum Circuit (CNOT counts)= 0):
     ┌───┐              
v_0: ┤ H ├──────────────
     ├───┤              
v_1: ┤ H ├──────────────
     ├───┤┌────────────┐
v_2: ┤ H ├┤ Rz(3.2015) ├
     ├───┤└────

In the following we print the values of the objective function of the quantum circuits designed along the path

In [21]:
quantum_circuit_path = best_path['qc']
cost = []
for i in range(len(quantum_circuit_path)):
    cost.append(problem(quantum_circuit_path[i], cost=True))
    print("Node at depth tree: ", i, "number of children: ", best_path["children"][i])
    print("Cost value: ", cost[i])
    print("Cumulative Reward: ", best_path["value"][i])
    print("Average Reward: ", best_path["value"][i]/best_path["visits"][i], "\n")

Node at depth tree:  0 number of children:  27
Cost value:  -0.04207897977473338
Cumulative Reward:  2101.276071495211
Average Reward:  0.4201711800630296 

Node at depth tree:  1 number of children:  27
Cost value:  -0.21523780602353038
Cumulative Reward:  2092.5719668818724
Average Reward:  0.43897041470146264 

Node at depth tree:  2 number of children:  27
Cost value:  -0.5924070087623008
Cumulative Reward:  2060.365291011336
Average Reward:  0.45163640749919687 

Node at depth tree:  3 number of children:  27
Cost value:  -0.5924070087623008
Cumulative Reward:  2003.5251787186753
Average Reward:  0.46313573248235673 

Node at depth tree:  4 number of children:  27
Cost value:  -0.7909784696632238
Cumulative Reward:  1935.8268489227034
Average Reward:  0.47192268379393065 

Node at depth tree:  5 number of children:  27
Cost value:  -0.7909784696632236
Cumulative Reward:  1855.7384390330267
Average Reward:  0.4789002423311037 

Node at depth tree:  6 number of children:  27
Cost va

At this poit we selct the ansatz as the best quantum circuit found in the path.

In [22]:
ansatz = quantum_circuit_path[cost.index(min(cost))]
print("Selected Ansatz: \n", ansatz)

Selected Ansatz: 
      ┌───┐┌────────────┐┌───────────┐┌─────────────┐
v_0: ┤ H ├┤ Rz(5.8983) ├┤ Rx(2.149) ├┤ Ry(0.17888) ├
     ├───┤└┬─────────┬─┘└───────────┘└─────────────┘
v_1: ┤ H ├─┤ Ry(1.4) ├──────────────────────────────
     ├───┤┌┴─────────┴─┐                            
v_2: ┤ H ├┤ Ry(5.0923) ├──────■─────────────────────
     ├───┤└────────────┘    ┌─┴─┐     ┌────────────┐
v_3: ┤ H ├──────────────────┤ X ├─────┤ Ry(4.6625) ├
     └───┘                  └───┘     └────────────┘


## Parameter Optimization
Finally we optimize the parameters through a classical optimizer according to the objective function to minimize

In [23]:
problem(quantum_circuit=ansatz, gradient=True)

Step = 0,  Energy = -0.94107005 Ha
Step = 2,  Energy = -0.95448783 Ha
Step = 4,  Energy = -0.96735727 Ha
Step = 6,  Energy = -0.97967370 Ha
Step = 8,  Energy = -0.99146588 Ha
Step = 10,  Energy = -1.00275192 Ha
Step = 12,  Energy = -1.01351143 Ha
Step = 14,  Energy = -1.02370795 Ha
Step = 16,  Energy = -1.03331362 Ha
Step = 18,  Energy = -1.04231981 Ha
Step = 20,  Energy = -1.05073577 Ha
Step = 22,  Energy = -1.05857665 Ha
Step = 24,  Energy = -1.06585059 Ha
Step = 26,  Energy = -1.07255693 Ha
Step = 28,  Energy = -1.07869387 Ha
Step = 30,  Energy = -1.08426631 Ha
Step = 32,  Energy = -1.08928783 Ha
Step = 34,  Energy = -1.09377673 Ha
Step = 36,  Energy = -1.09775171 Ha
Step = 38,  Energy = -1.10123266 Ha
Step = 40,  Energy = -1.10424477 Ha
Step = 42,  Energy = -1.10682078 Ha
Step = 44,  Energy = -1.10899873 Ha
Step = 46,  Energy = -1.11081791 Ha
Step = 48,  Energy = -1.11231674 Ha
Step = 50,  Energy = -1.11353343 Ha
Step = 52,  Energy = -1.11450648 Ha
Step = 54,  Energy = -1.11527313 

[array(-0.93416621),
 array(-0.94107005),
 array(-0.94784572),
 array(-0.95448783),
 array(-0.96099235),
 array(-0.96735727),
 array(-0.97358327),
 array(-0.9796737),
 array(-0.98563328),
 array(-0.99146588),
 array(-0.99717268),
 array(-1.00275192),
 array(-1.00819976),
 array(-1.01351143),
 array(-1.01868219),
 array(-1.02370795),
 array(-1.02858567),
 array(-1.03331362),
 array(-1.0378914),
 array(-1.04231981),
 array(-1.04660057),
 array(-1.05073577),
 array(-1.05472733),
 array(-1.05857665),
 array(-1.06228439),
 array(-1.06585059),
 array(-1.0692749),
 array(-1.07255693),
 array(-1.07569649),
 array(-1.07869387),
 array(-1.08154998),
 array(-1.08426631),
 array(-1.08684483),
 array(-1.08928783),
 array(-1.09159768),
 array(-1.09377673),
 array(-1.09582729),
 array(-1.09775171),
 array(-1.09955253),
 array(-1.10123266),
 array(-1.10279544),
 array(-1.10424477),
 array(-1.10558499),
 array(-1.10682078),
 array(-1.10795705),
 array(-1.10899873),
 array(-1.10995075),
 array(-1.110817